In [ ]:
import numpy as np
import os
import glob 
import time 
import pandas as pd
import shutil
import re
import mdtraj as md
import MDAnalysis as mda
import pickle
import pickle as p 
import csv
import sys
import subprocess
import xml.etree.ElementTree as ET
import requests
import concurrent.futures
import multiprocessing
import nglview as nv
import h5py
import matplotlib as mpl
import matplotlib.patheffects as path_effects
import matplotlib.patches as patches
import html
import biobox as bb
import tempfile
import matplotlib.pyplot as plt
import molearn
import torch
import glob as glob
import MDAnalysis.analysis.rms as rms
import seaborn as sns
import pickle
import networkx as nx
sys.path.insert(0, os.path.join(os.path.abspath(os.pardir),'src'))

from Bio import PDB
from tqdm import tqdm
from time import time as t
from urllib.request import urlretrieve as download
from Bio.Blast import NCBIWWW, NCBIXML
from Bio.Blast.Applications import NcbipsiblastCommandline
from collections import defaultdict
from Bio.PDB import PPBuilder
from Bio.SeqUtils import seq1
from modeller import *
from modeller.automodel import *
from Bio.PDB import PDBParser
from MDAnalysis.analysis import align
from mpi4py import MPI
from glob import glob
from pprint import pprint as pp
from matplotlib import pyplot as plt
from sklearn.decomposition import PCA
from glob import glob as g
from tqdm.notebook import tqdm
from collections import Counter
from matplotlib.ticker import FuncFormatter
from collections import defaultdict
from pymol import cmd
from scipy.interpolate import interp1d
from mpl_toolkits import mplot3d
from scipy import stats
from sklearn.cluster import AgglomerativeClustering, SpectralClustering
from matplotlib.colors import BoundaryNorm
from numpy.linalg import norm
from molearn.data import PDBData
from molearn.trainers import Trainer
from molearn.models.small_foldingnet import Small_AutoEncoder
from molearn.analysis.analyser import MolearnAnalysis
from copy import deepcopy
from molearn.analysis import MolearnGUI
from scipy.ndimage import rotate
from numpy.linalg import inv
from sklearn.cluster import HDBSCAN
from sklearn.metrics import silhouette_score
from itertools import combinations
from urllib.request import urlretrieve
from urllib.error import URLError
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, confusion_matrix, precision_score, recall_score, ConfusionMatrixDisplay
from sklearn.inspection import permutation_importance
from sklearn.tree import export_graphviz
from sklearn import tree
from scipy.stats import pearsonr


Downloads structures according to text file 'structure-matching-IPR011009.tsv' obtained from interpro.

In [2]:
structure_path = 'structure-matching-IPR011009.tsv'
pdb_data = pd.read_csv(structure_path, sep = "\t", header=0, engine='python')
pdb_data['Accession'] = pdb_data['Accession'].str.upper()

In [ ]:
def download2(code, pdir=None, max_retries=3):
    """Download a PDB file with retry mechanism and failure handling"""
    base_url = "https://files.rcsb.org/download"
    pdb_url = f"{base_url}/{code}.pdb"
    f_p = os.path.join(pdir, f"{code}.pdb")

    for attempt in range(max_retries):
        try:
            response = requests.get(pdb_url, stream=True, timeout=10)
            if response.status_code == 404:
                print(f"{code} does not exist (404 Not Found)")
                return None
            response.raise_for_status()
            
            with open(f_p, "wb") as f:
                for chunk in response.iter_content(chunk_size=8192):
                    f.write(chunk)

            # Check file size to prevent empty files
            if os.path.getsize(f_p) == 0:
                print(f"{code}.pdb download failed (empty file), retrying {attempt+1}/{max_retries}...")
                os.remove(f_p)
                continue  # Retry

            print(f"{code}.pdb downloaded successfully")
            return f_p
        except requests.exceptions.RequestException as e:
            print(f"{code}.pdb download failed, retrying {attempt+1}/{max_retries}... Error: {e}")
            time.sleep(2)

    print(f"{code}.pdb download ultimately failed")
    return None


def download_pdbs(pdb_list, pdir=None):
    """Download multiple PDB files"""
    default_dir = "./PDBs"
    pdir = os.path.abspath(pdir if pdir else default_dir)
    os.makedirs(pdir, exist_ok=True)

    # Get already downloaded PDB files to avoid duplicate downloads
    existing_files = {os.path.splitext(f)[0] for f in os.listdir(pdir)}

    for code in pdb_list:
        if code not in existing_files:
            file_path = download2(code, pdir=pdir)
            if file_path:
                print(f"{code} downloaded successfully")
            else:
                print(f"{code} download failed")


def parallel_download(pdb_list, pdir=None):
    """Download PDB files in parallel"""
    num_workers = min(20, multiprocessing.cpu_count()*2)  # Limit the number of threads
    chunk_size = max(10, len(pdb_list) // num_workers)  # Each thread handles at least 10 PDB files

    splited_pdb_lists = [pdb_list[i:i+chunk_size] for i in range(0, len(pdb_list), chunk_size)]

    with concurrent.futures.ThreadPoolExecutor(max_workers=num_workers) as executor:
        executor.map(download_pdbs, splited_pdb_lists)

In [4]:
pdbs_ids = pdb_data['Accession'].tolist()
parallel_download(pdbs_ids)

7BKN.pdb downloaded successfully
7BKN downloaded successfully
2X4Z.pdb downloaded successfully
2X4Z downloaded successfully
1A06.pdb downloaded successfully
1A06 downloaded successfully
3R1Q.pdb downloaded successfully
3R1Q downloaded successfully
3GU7.pdb downloaded successfully
3GU7 downloaded successfully
4C38.pdb downloaded successfully
4C38 downloaded successfully
8I80.pdb downloaded successfully
8I80 downloaded successfully
5O11.pdb downloaded successfully
5O11 downloaded successfully
4J52.pdb downloaded successfully
4J52 downloaded successfully
5FBL.pdb downloaded successfully
5FBL downloaded successfully
2CHZ.pdb downloaded successfully
2CHZ downloaded successfully
7TYM.pdb downloaded successfully
7TYM downloaded successfully
4UY9.pdb downloaded successfully
4UY9 downloaded successfully
5X3F.pdb downloaded successfully
5X3F downloaded successfully
6T8X.pdb downloaded successfully
6T8X downloaded successfully
6HMQ.pdb downloaded successfully
6HMQ downloaded successfully
7BKO.pdb

Counting the number of pdb files in the directory PDBs

In [5]:
folder_path = "PDBs"
file_names = [os.path.splitext(f)[0] for f in os.listdir(folder_path) if os.path.isfile(os.path.join(folder_path, f))]
pdb_raw = pd.DataFrame({"PDBs": file_names})

pdb_data['Downloaded'] = pdb_data['Accession'].str.upper().isin(pdb_raw['PDBs']).map({True: True, False: False})

counts = pdb_data['Downloaded'].value_counts().to_dict()
print(f"Downloaded: {counts[True]}, Failed: {counts[False]}")

Downloaded: 8054, Failed: 169


Saving the names of failed pdb downloads.

In [6]:
fail_list = pdb_data[pdb_data['Downloaded']==False]
fail_list.to_csv('fail_list.csv')

Strip the downloaded pdb files to only contain the chain of interest

In [ ]:
import sys
import subprocess
 
python_executable = sys.executable

cmd = [python_executable, "strip_pdb.py"]
result = subprocess.run(cmd, capture_output=True, text=True)

print(result.stdout)
print(result.stderr)

Skipping Results/activation_segments/unaligned/1A06_A.pdb: already exists
Skipping Results/activation_segments/unaligned/1QPD_A.pdb: already exists
Skipping Results/activation_segments/unaligned/3GB2_A.pdb: already exists
Skipping Results/activation_segments/unaligned/2P4I_A.pdb: already exists
Skipping Results/activation_segments/unaligned/2P4I_B.pdb: already exists
Skipping Results/activation_segments/unaligned/3MJW_A.pdb: already exists
Skipping Results/activation_segments/unaligned/2WXK_A.pdb: already exists
Skipping Results/activation_segments/unaligned/3C50_A.pdb: already exists
Skipping Results/activation_segments/unaligned/3C50_B.pdb: already exists
Skipping Results/activation_segments/unaligned/2CCI_A.pdb: already exists
Skipping Results/activation_segments/unaligned/2CCI_C.pdb: already exists
Skipping Results/activation_segments/unaligned/1A9U_A.pdb: already exists
Skipping Results/activation_segments/unaligned/1QPE_A.pdb: already exists
Skipping Results/activation_segments/u

Count again how many pdb files are in the directory after stripping the chains

In [ ]:
import glob
def count_pdb_files(directory):
    directory = os.path.join(directory, '')

    pdb_files = glob.glob(os.path.join(directory, '*.pdb'))

    return len(pdb_files)

pdb_directory = 'Results/activation_segments/unaligned/'

pdb_count = count_pdb_files(pdb_directory)

print(f"There are {pdb_count} PDB files in the directory '{pdb_directory}'.")

There are 12312 PDB files in the directory 'Results/activation_segments/unaligned/'.


Filtering of Residues

In [ ]:
"""
This script extracts the DFG–APE region from multiple protein structures and aligns the SEQRES and ATOM sequences to identify structures with small gaps and good sequence matches. Matched structures are recorded with alignment details and their full sequences are saved to a FASTA file.

"""

def substitute_non_natural_amino_acid(residue, aligned_atom, index):
    """Substitute non-natural amino acids with their natural counterparts."""
    substitutions = {
        'X': 'G',  # Glycine
        'B': 'N',  # Asparagine
        'Z': 'Q',  # Glutamine
        'J': 'L'   # Leucine
    }
    
    if residue == 'X':
        # Check if 'X' is surrounded by missing amino acids in aligned_atom
        if index > 0 and aligned_atom[index - 1] == '-':
            return residue
        if index < len(aligned_atom) - 1 and aligned_atom[index + 1] == '-':
            return residue

    return substitutions.get(residue, residue)

def extract_seqres_sequence(pdb_file):
    """Extract SEQRES sequences from the full PDB file, grouped by chain."""
    seq_dict = {}
    with open(pdb_file, "r") as file:
        lines = file.readlines()

    current_chain = None
    current_seq = []

    for line in lines:
        if line.startswith("SEQRES"):
            parts = line.split()
            chain_id = parts[2]
            if chain_id != current_chain:
                if current_chain is not None:
                    seq_dict[current_chain] = ''.join(seq1(residue) for residue in current_seq)
                current_chain = chain_id
                current_seq = []
            current_seq.extend(parts[4:])

    if current_chain is not None:
        seq_dict[current_chain] = ''.join(seq1(residue) for residue in current_seq)

    return seq_dict

def extract_atom_sequence(pdb_file, chain_id):
    """Extract actual ATOM-based sequence from coordinates for a given chain."""
    parser = PDBParser(QUIET=True)
    structure = parser.get_structure('PDB', pdb_file)
    
    for model in structure:
        chain = model[chain_id]
        
        ppb = PPBuilder()
        sequence = ''
        for pp in ppb.build_peptides(chain):
            sequence += pp.get_sequence()
        return sequence
    return None

def find_motif_indices(sequence, motif):

    index = sequence.find(motif)
    return index if index != -1 else None

def align_and_highlight_gaps(seqres_segment, atom_segment):
    """Perform simple alignment and compute the max length of gaps in the atom sequence."""
    aligned_seqres = ''
    aligned_atom = ''
    atom_index = 0
    max_gap_length = 0
    current_gap_length = 0

    for res_seqres in seqres_segment:
        if atom_index < len(atom_segment) and res_seqres == atom_segment[atom_index]:
            aligned_seqres += res_seqres
            aligned_atom += atom_segment[atom_index]
            atom_index += 1
            current_gap_length = 0
        else:
            aligned_seqres += res_seqres
            aligned_atom += '-'
            current_gap_length += 1
            max_gap_length = max(max_gap_length, current_gap_length)

    return aligned_seqres, aligned_atom, max_gap_length

def main():
    target_dir = "Results/activation_segments/unaligned"
    pdb_dir = "PDBs"
    fasta_output_file = "seqres_sequences.fasta"  # File to store full sequences
    text_output_file = "seqres_info.txt"
    aligned_sequences = {}
    satisfying_structures_count = 0

    pdb_files = glob.glob(os.path.join(target_dir, "*.pdb"))

    with open(text_output_file, "w") as text_output, open(fasta_output_file, "w") as fasta_output:
        for pdb_file in tqdm(pdb_files, desc="Processing PDB files"):
            pdb_name = os.path.basename(pdb_file)
            pdb_id, chain_id_file = os.path.splitext(pdb_name)[0].split('_')
            chain_id = chain_id_file

            full_pdb_path = os.path.join(pdb_dir, pdb_id + '.pdb')
            if not os.path.isfile(full_pdb_path):
                print(f"Corresponding full PDB for {pdb_id} not found.")
                continue

            seqres_seqs = extract_seqres_sequence(full_pdb_path)
            atom_seq = extract_atom_sequence(full_pdb_path, chain_id)

            if chain_id in seqres_seqs and atom_seq:
                seqres_sequence = seqres_seqs[chain_id]
                seqres_dfg_index = find_motif_indices(seqres_sequence, 'DFG')
                seqres_ape_index = find_motif_indices(seqres_sequence, 'APE')
                atom_dfg_index = find_motif_indices(atom_seq, 'DFG')
                atom_ape_index = find_motif_indices(atom_seq, 'APE')

                if None not in [seqres_dfg_index, seqres_ape_index, atom_dfg_index, atom_ape_index]:
                    seqres_start = min(seqres_dfg_index, seqres_ape_index)
                    seqres_end = max(seqres_dfg_index + 3, seqres_ape_index + 3)
                    atom_start = min(atom_dfg_index, atom_ape_index)
                    atom_end = max(atom_dfg_index + 3, atom_ape_index + 3)

                    seqres_segment = seqres_sequence[seqres_start:seqres_end]
                    atom_segment = atom_seq[atom_start:atom_end]

                    aligned_seqres, aligned_atom, max_gap_length = align_and_highlight_gaps(seqres_segment, atom_segment)
                    
                    exclude_due_to_non_natural_diff = False
                    corrected_seqres = ''
                    for index, (res_seqres, res_atom) in enumerate(zip(aligned_seqres, aligned_atom)):
                        if res_seqres != res_atom:
                            corrected_residue = substitute_non_natural_amino_acid(res_seqres, aligned_atom, index)
                            corrected_seqres += corrected_residue
                            if corrected_residue != res_seqres:
                                print(f"Substituting non-natural amino acid '{res_seqres}' with '{corrected_residue}' in SEQRES for {pdb_id}_{chain_id}.")
                        else:
                            corrected_seqres += res_seqres

                    if not exclude_due_to_non_natural_diff and max_gap_length <= 4:
                        satisfying_structures_count += 1
                        info = (f"Aligned Sequences for {pdb_id}_{chain_id}: (Max gap length: {max_gap_length})\n"
                                f"SEQRES Segment: {corrected_seqres}\n"
                                f"ATOM Segment:   {aligned_atom}\n\n")
                        print(info)
                        text_output.write(info)
                        
                        aligned_sequences[f"{pdb_id}_{chain_id}_SEQRES"] = corrected_seqres
                        aligned_sequences[f"{pdb_id}_{chain_id}_ATOM"] = aligned_atom

                        fasta_output.write(f">{pdb_id}_{chain_id}_SEQRES\n{seqres_sequence}\n")
                        fasta_output.write(f">{pdb_id}_{chain_id}_ATOM\n{atom_seq}\n")
                    else:
                        exclusion_msg = f"Excluding {pdb_id}_{chain_id} due to gap length: {max_gap_length} or non-natural amino acid difference.\n"
                        print(exclusion_msg)
                        text_output.write(exclusion_msg)
                else:
                    motif_msg = f"Motifs not found in {pdb_id}_{chain_id}.\n"
                    print(motif_msg)
                    text_output.write(motif_msg)
            else:
                chain_msg = f"Chain {chain_id} not found in SEQRES of {pdb_id} or no atomic sequence available.\n"
                print(chain_msg)
                text_output.write(chain_msg)
                
        count_msg = f"Total structures satisfying the condition: {satisfying_structures_count}"
        text_output.write(count_msg)
        print(count_msg)

if __name__ == '__main__':
    main()


Processing PDB files:   0%|          | 0/12312 [00:00<?, ?it/s]

Motifs not found in 1A06_A.

Aligned Sequences for 1A9U_A: (Max gap length: 0)
SEQRES Segment: DFGLARHTDDEMTGYVATRWYRAPE
ATOM Segment:   DFGLARHTDDEMTGYVATRWYRAPE


Aligned Sequences for 1AD5_A: (Max gap length: 0)
SEQRES Segment: DFGLARVGAKFPIKWTAPE
ATOM Segment:   DFGLARVGAKFPIKWTAPE


Aligned Sequences for 1AD5_B: (Max gap length: 0)
SEQRES Segment: DFGLARVGAKFPIKWTAPE
ATOM Segment:   DFGLARVGAKFPIKWTAPE


Aligned Sequences for 1AGW_A: (Max gap length: 0)
SEQRES Segment: DFGLARDIHHIDYYKKTTNGRLPVKWMAPE
ATOM Segment:   DFGLARDIHHIDYYKKTTNGRLPVKWMAPE


Excluding 1AGW_B due to gap length: 5 or non-natural amino acid difference.

Substituting non-natural amino acid 'X' with 'G' in SEQRES for 1APM_E.
Aligned Sequences for 1APM_E: (Max gap length: 1)
SEQRES Segment: DFGFAKRVKGRTWGLCGTPEYLAPE
ATOM Segment:   DFGFAKRVKGRTW-LCGTPEYLAPE


Excluding 1AQ1_A due to gap length: 13 or non-natural amino acid difference.

Substituting non-natural amino acid 'X' with 'G' in SEQRES for 1ATP_E.
Aligned 

Count how many seqences are in the fasta file

In [7]:
#COunting how many seqences are in the fasta file
def count_total_pdb_ids(file_path):
    total_pdb_ids = 0

    with open(file_path, 'r') as file:
        for line in file:
            if line.startswith('>'):
                total_pdb_ids += 1

    print(f"Total number of PDB IDs: {int(total_pdb_ids/2)} in {file_path}") #here we divide by 2 because we have two lines per PDB ID

# Provide the path to your seqres_sequence.fasta file
file_path = "seqres_sequences.fasta"
count_total_pdb_ids(file_path)


Total number of PDB IDs: 3845 in seqres_sequences.fasta


Use MODELLER to reconstruct structures in their entirety.

In [ ]:
"""
This script processes the DFG–APE region of kinase structures. It compares the SEQRES sequence from a FASTA file with the ATOM sequence from a PDB file, and if differences are found, it uses MODELLER to reconstruct the missing parts. The completed models are saved for further analysis.
"""
def read_fasta_sequences(fasta_file):
    # Read sequences from a FASTA file and store them in a dictionary {header: sequence}
    sequences = {}
    with open(fasta_file, "r") as f:
        lines = f.readlines()
        header = None
        sequence = []
        for line in lines:
            line = line.strip()
            if line.startswith(">"):
                if header:
                    sequences[header] = ''.join(sequence)
                header = line[1:]
                sequence = []
            else:
                sequence.append(line)
        if header:
            sequences[header] = ''.join(sequence)
    return sequences

def extract_atom_sequence(pdb_file):
    # Extract ATOM-based protein sequence from a PDB structure using Biopython
    parser = PDBParser(QUIET=True)
    structure = parser.get_structure('PDB', pdb_file)
    
    for model in structure:
        for chain in model:
            ppb = PPBuilder()
            sequence = ''
            for pp in ppb.build_peptides(chain):
                sequence += pp.get_sequence()
            return str(sequence)
    return None

def find_motif_indices(sequence, motif):
    # Locate the starting index of the specified motif (e.g., 'DFG' or 'APE') within the sequence
    index = sequence.find(motif)
    return index if index != -1 else None

def reconstruct_with_modeller(pdb_chain_id, pdb_path, target_path, full_sequence, atom_sequence):
    print(f"Processing {pdb_chain_id}")

    seqres_dfg_index = find_motif_indices(full_sequence, 'DFG')
    seqres_ape_index = find_motif_indices(full_sequence, 'APE')
    atom_dfg_index = find_motif_indices(atom_sequence, 'DFG')
    atom_ape_index = find_motif_indices(atom_sequence, 'APE')

    if None not in [seqres_dfg_index, seqres_ape_index, atom_dfg_index, atom_ape_index]:
        seqres_start = min(seqres_dfg_index, seqres_ape_index)
        seqres_end = max(seqres_dfg_index + 3, seqres_ape_index + 3)
        atom_start = min(atom_dfg_index, atom_ape_index)
        atom_end = max(atom_dfg_index + 3, atom_ape_index + 3)

        seqres_segment = full_sequence[seqres_start:seqres_end]
        atom_segment = atom_sequence[atom_start:atom_end]

        if seqres_segment != atom_segment:
            print(f"Reconstructing full sequence for {pdb_chain_id} using MODELLER")

            env = environ()
            aln = alignment(env)

            mdl = model(env, file=pdb_path)
            aln.append_model(mdl, align_codes='template', atom_files=pdb_path)

            aln.append_sequence(full_sequence)
            aln[-1].code = 'target'

            aln.align2d(max_gap_length=50)

            # Perform comparative modeling to build a complete model including missing residues
            a = automodel(env, alnfile=aln, knowns='template', sequence='target')
            a.starting_model = 1
            a.ending_model = 1
    
            a.make()

            model_path = os.path.join(target_path, f"{pdb_chain_id}_filled.pdb")
            os.rename(a.outputs[0]['name'], model_path)
            print(f"Reconstruction completed for {pdb_chain_id}. File saved at {model_path}")

            remove_remark_lines(model_path)
        else:
            shutil.copy(pdb_path, os.path.join(target_path, f"{pdb_chain_id}.pdb"))
            print(f"No differences found for {pdb_chain_id}. Original PDB copied to target directory.")
    else:
        print(f"Motifs not found in {pdb_chain_id}.")

def remove_remark_lines(pdb_file):
    # Clean the PDB file by removing all REMARK lines after modeling
    with open(pdb_file, 'r') as file:
        lines = file.readlines()
    
    with open(pdb_file, 'w') as file:
        for line in lines:
            if not line.startswith("REMARK"):
                file.write(line)
    
    print(f"Removed REMARK lines from {pdb_file}")

def main():
    seqres_fasta = "seqres_sequences.fasta"
    pdb_dir = "Results/activation_segments/unaligned"
    target_dir = "Results/activation_segments/reconstructedModeller"

    seqres_sequences = read_fasta_sequences(seqres_fasta)

    if not os.path.exists(target_dir):
        os.makedirs(target_dir)

    for header, full_sequence in seqres_sequences.items():
        if "_SEQRES" in header:  
            pdb_chain_id = header.replace("_SEQRES", "")
            pdb_file_path = os.path.join(pdb_dir, f"{pdb_chain_id}.pdb")

            target_filled_path = os.path.join(target_dir, f"{pdb_chain_id}_filled.pdb")
            target_original_path = os.path.join(target_dir, f"{pdb_chain_id}.pdb")
            if os.path.exists(target_filled_path) or os.path.exists(target_original_path):
                print(f"Skipping {pdb_chain_id}: already exists in target directory.")
                continue
            
            # Extract existing sequence from ATOM records in the PDB
            atom_sequence = extract_atom_sequence(pdb_file_path)
            
            if atom_sequence is None:
                print(f"Could not extract sequence for {pdb_chain_id}. Skipping...")
                continue

            if not os.path.exists(target_dir):
                os.makedirs(target_dir)
            
            reconstruct_with_modeller(pdb_chain_id, pdb_file_path, target_dir, full_sequence, atom_sequence)

    print("Processing complete!")

if __name__ == '__main__':
    main()

Skipping 1A9U_A: already exists in target directory.
Skipping 1AD5_A: already exists in target directory.
Skipping 1AD5_B: already exists in target directory.
Skipping 1AGW_A: already exists in target directory.
Skipping 1APM_E: already exists in target directory.
Skipping 1ATP_E: already exists in target directory.
Skipping 1B38_A: already exists in target directory.
Skipping 1B39_A: already exists in target directory.
Skipping 1BI7_A: already exists in target directory.
Skipping 1BI8_A: already exists in target directory.
Skipping 1BI8_C: already exists in target directory.
Skipping 1BKX_A: already exists in target directory.
Skipping 1BL6_A: already exists in target directory.
Skipping 1BL7_A: already exists in target directory.
Skipping 1BLX_A: already exists in target directory.
Skipping 1BMK_A: already exists in target directory.
Skipping 1BUH_A: already exists in target directory.
Skipping 1BX6_A: already exists in target directory.
Skipping 1CDK_A: already exists in target dire

Counting number of PDBs after reconstruction

In [ ]:
import glob

def count_pdb_files(directory):
    directory = os.path.join(directory, '')
    pdb_files = glob.glob(os.path.join(directory, '*.pdb'))
    return len(pdb_files)

pdb_directory = 'Results/activation_segments/reconstructedModeller'

pdb_count = count_pdb_files(pdb_directory)

print(f"There are {pdb_count} PDB files in the directory '{pdb_directory}'.")


There are 3845 PDB files in the directory 'Results/activation_segments/reconstructedModeller'.


In [ ]:

three_to_one = {
    'ALA': 'A', 'ARG': 'R', 'ASN': 'N', 'ASP': 'D',
    'CYS': 'C', 'GLU': 'E', 'GLN': 'Q', 'GLY': 'G',
    'HIS': 'H', 'ILE': 'I', 'LEU': 'L', 'LYS': 'K',
    'MET': 'M', 'PHE': 'F', 'PRO': 'P', 'SER': 'S',
    'THR': 'T', 'TRP': 'W', 'TYR': 'Y', 'VAL': 'V'
}

def extract_sequence_and_mapping(pdb_file):
    parser = PDBParser(QUIET=True)
    structure = parser.get_structure('PDB', pdb_file)
    
    sequence = []
    index_to_resid = {}
    
    for model in structure:
        for chain in model:
            for residue in chain:
                if 'CA' in residue:  # Check if it's an amino acid
                    resname = residue.get_resname()
                    if resname in three_to_one:
                        sequence.append(three_to_one[resname])
                        index_to_resid[len(sequence) - 1] = residue.get_id()[1]  # Map sequence index to PDB resid
            break
        break

    return sequence, index_to_resid

def find_motif_indices(sequence, motif):
    """Find the start index of a motif in a sequence."""
    sequence_str = ''.join(sequence)
    index = sequence_str.find(motif)
    return index if index != -1 else None

# Extract sequence and map sequence indices to PDB residue IDs for locating specific motifs
atom_sequence, index_to_resid = extract_sequence_and_mapping("Results/activation_segments/unaligned/7OPO_A.pdb")

# Find indices of DFG and APE motifs
dfg_index = find_motif_indices(atom_sequence, 'DFG')
ape_index = find_motif_indices(atom_sequence, 'APE')

if dfg_index is not None and ape_index is not None:
    # Identify the corresponding PDB residue IDs of the DFG and APE motifs
    dfg_resid = index_to_resid[dfg_index]
    ape_resid = index_to_resid[ape_index + 2]  

    u_missing = mda.Universe("Results/activation_segments/unaligned/7OPO_A.pdb")
    selected_atoms = u_missing.select_atoms(f"resid {dfg_resid}:{ape_resid}")

    print("Number of Atoms Selected:", selected_atoms.n_atoms)

    u_reconstructed = mda.Universe("Results/activation_segments/reconstructedModeller/7OPO_A_filled.pdb")
    print("Number of Atoms Reconstructed:", u_reconstructed.select_atoms(f"all").n_atoms)

    merged = mda.Merge(selected_atoms, u_reconstructed.atoms)
    print(merged.residues)

    w = nv.show_mdanalysis(merged)

    w.clear()
    w.add_cartoon(color="resname")

    

else:
    print("Motifs not found in the sequence.")

w

Number of Atoms Selected: 206
Number of Atoms Reconstructed: 2558
<ResidueGroup [<Residue ASP, 211>, <Residue PHE, 212>, <Residue GLY, 213>, ..., <Residue GLY, 315>, <Residue ARG, 316>, <Residue PRO, 317>]>


NGLWidget()

In [ ]:
"""
Count how many PDB files did not require reconstruction (i.e., without '_filled' in their names).

"""

def count_non_filled_pdbs(directory):
    pdb_files = g(os.path.join(directory, "*.pdb"))

    non_filled_pdbs = [pdb for pdb in pdb_files if "_filled" not in os.path.basename(pdb)]

    return len(non_filled_pdbs)

pdb_directory_path = 'Results/activation_segments/reconstructedModeller'

# Get the count of non '_filled' PDB files
non_filled_pdb_count = count_non_filled_pdbs(pdb_directory_path)

print(f"There are {non_filled_pdb_count} PDB files without '_filled' in the directory '{pdb_directory_path}'.")


There are 1977 PDB files without '_filled' in the directory 'Results/activation_segments/reconstructedModeller'.
